In [1]:
# Import packages
library(rstan)
library(coda)
library(parallel)
library(Bessel)

Loading required package: StanHeaders
Loading required package: ggplot2
Registered S3 methods overwritten by 'ggplot2':
  method         from 
  [.quosures     rlang
  c.quosures     rlang
  print.quosures rlang
rstan (Version 2.19.2, GitRev: 2e1f913d3ca3)
For execution on a local, multicore CPU with excess RAM we recommend calling
options(mc.cores = parallel::detectCores()).
To avoid recompilation of unchanged Stan programs, we recommend calling
rstan_options(auto_write = TRUE)
For improved execution time, we recommend calling
Sys.setenv(LOCAL_CPPFLAGS = '-march=native')
although this causes Stan to throw an error on a few processors.

Attaching package: 'coda'

The following object is masked from 'package:rstan':

    traceplot



In [2]:
# add path required by rstan
library(devtools) 
Sys.setenv(PATH = paste("C:/Rtools/bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(PATH = paste("C:\\Rtools\\mingw_64\\bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(BINPREF = "C:/Rtools/mingw_$(WIN)/bin/")

Loading required package: usethis


# Read csv into dataframe

In [3]:
dat.str <- Sys.glob("data.*.csv")
data <- as.data.frame(read.csv(file = dat.str))
# slicing training set (whole 2018 season)
dat <- data[data$period < 27,]

In [4]:
head(dat)

X   Date       Season round period home.name away.name home.score
154 172 2018-04-08 2018   3     26     WC        GE         95       
155 173 2018-04-08 2018   3     26     WB        ES        104       
156 174 2018-04-08 2018   3     26     RI        HW        102       
157 175 2018-04-07 2018   3     26     SK        AD         55       
158 176 2018-04-07 2018   3     26     SY        GW        103       
159 177 2018-04-07 2018   3     26     GC        FR         68       
    away.score home.goals ... Total.Score.Over.Min Total.Score.Over.Max
154  80        14         ... 1.9                  1.9                 
155  83        14         ... 1.9                  1.9                 
156  89        15         ... 1.9                  1.9                 
157 104         7         ... 1.9                  1.9                 
158  87        16         ... 1.9                  1.9                 
159  96        10         ... 1.9                  1.9                 
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
154 1.9                    1.9                    1.9                  
155 1.9                    1.9                    1.9                  
156 1.9                    1.9                    1.9                  
157 1.9                    1.9                    1.9                  
158 1.9                    1.9                    1.9                  
159 1.9                    1.9                    1.9                  
    Total.Score.Under.Max Total.Score.Under.Close Notes home.number away.number
154 1.9                   1.9                           17           9         
155 1.9                   1.9                           16           6         
156 1.9                   1.9                            8          14         
157 1.9                   1.9                            2           7         
158 1.9                   1.9                            5           1         
159 1.9                   1.9                           18           3

In [5]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

In [82]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

# home.number <- vector()
# away.number <- vector()

# for (i in 1:nrow(dat)){
#     home.number <- append(home.number, h[[as.character(dat$home.name[i])]])
#     away.number <- append(away.number, h[[as.character(dat$away.name[i])]])
    
# }

# dat$home.number <- home.number
# dat$away.number <- away.number

In [84]:
# write.csv(dat, 'temp.csv')

# 2019 Round 1 data

In [5]:
matchup <- data[data$period == 27,]
n.matches <- length(matchup$home.number)
matchup

X   Date       Season round period home.name away.name home.score
145 163 2018-04-15 2018   4     27     GE        SK        103       
146 164 2018-04-15 2018   4     27     HW        ME        115       
147 165 2018-04-15 2018   4     27     ES        PA        106       
148 166 2018-04-14 2018   4     27     WC        GC        139       
149 167 2018-04-14 2018   4     27     NM        CA        116       
150 168 2018-04-14 2018   4     27     WB        SY         79       
151 169 2018-04-14 2018   4     27     RI        BL        110       
152 170 2018-04-14 2018   4     27     GW        FR         82       
153 171 2018-04-13 2018   4     27     AD        CW         58       
    away.score home.goals ... Total.Score.Over.Min Total.Score.Over.Max
145  56        15         ... 1.9                  1.9                 
146  48        18         ... 1.9                  1.9                 
147  84        16         ... 1.9                  1.9                 
148  59        21         ... 1.9                  1.9                 
149  30        18         ... 1.9                  1.9                 
150  86        11         ... 1.9                  1.9                 
151  17        16         ... 1.9                  1.9                 
152  51        11         ... 1.9                  1.9                 
153 106         9         ... 1.9                  1.9                 
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
145 1.9                    1.9                    1.9                  
146 1.9                    1.9                    1.9                  
147 1.9                    1.9                    1.9                  
148 1.9                    1.9                    1.9                  
149 1.9                    1.9                    1.9                  
150 1.9                    1.9                    1.9                  
151 1.9                    1.9                    1.9                  
152 1.9                    1.9                    1.9                  
153 1.9                    1.9                    1.9                  
    Total.Score.Under.Max Total.Score.Under.Close Notes home.number away.number
145 1.9                   1.9                            8          16         
146 1.9                   1.9                            9          11         
147 1.9                   1.9                            5           3         
148 1.9                   1.9                            2          17         
149 1.9                   1.9                           12           4         
150 1.9                   1.9                            6           7         
151 1.9                   1.9                           15          18         
152 1.9                   1.9                           14          10         
153 1.9                   1.9                            1          13

# Data

In [6]:
home.name <- as.matrix(dat$home.name)
away.name <- as.matrix(dat$away.name)
home.numb <- dat$home.number
away.numb <- dat$away.number

home.Goals <- dat$home.goals
home.Behinds <- dat$home.behinds
away.Goals <- dat$away.goals
away.Behinds <- dat$away.behinds

period <- dat$period
n.teams <- 18
n.games <- length(home.numb)
n.periods <- max(period)
n.bps <- 2
bps <- c(1,24)

In [7]:
# matricies for the Owen paper centering
ones <- matrix(1, nrow = (n.teams-1), ncol = 1)
S_t <-  n.teams / (n.teams-1) * (diag(n.teams-1) + ones %*% t(ones))

# Jmat is n * n-1
J.up.left <- diag(n.teams-1) - (1/n.teams)*(ones %*% t(ones))
J.bot.left <- - t(ones) * 1/n.teams

Jmat <- rbind(J.up.left, J.bot.left)

# Store data into list required by STAN

In [8]:
dat.list <- list(N = n.teams,
                 G = n.games,
                 T = n.periods,
                 period = period,
                 home = home.numb,
                 away = away.numb,
                 homeGoals = home.Goals,
                 homeBehinds = home.Behinds,
                 awayGoals = away.Goals,
                 awayBehinds = away.Behinds,
                 BP = n.bps,
                 Breaks = bps,
                 Smat = S_t,
                 JmatTrans = t(Jmat),
                 N_Matches = n.matches,
                 nextHome = matchup$home.number,
                 nextAway = matchup$away.number)

# Compile the model

In [9]:
prefit <- stan("Skellam goal and behind difference.stan", data = dat.list, chains = 0)

DIAGNOSTIC(S) FROM PARSER:
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: assignment operator <- deprecated in the Stan language; use = instead.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # 

the number of chains is less than 1; sampling not done


# Sampling using MCMC (4 cores in parallel)

In [10]:
cl <- makeCluster(4)

clusterEvalQ(cl, library(rstan))

myfunction <- function(var1, var2, var3){
    stan(fit = var3, data = var2,
                            chains = 1, chain_id = var1, iter = 2500,
                            refresh = -1, init = "0")
}

sflist <- parLapply(cl, 1:4, fun = myfunction, var2 = dat.list, var3 = prefit)
stopCluster(cl)

[[1]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[2]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[3]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[4]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"

In [11]:
sflist

[[1]]
Inference for Stan model: Skellam goal and behind difference.
1 chains, each with iter=2500; warmup=1250; thin=1; 
post-warmup draws per chain=1250, total post-warmup draws=1250.

                           mean se_mean     sd   2.5%    25%    50%    75%
delta                      0.65    0.00   0.07   0.51   0.61   0.66   0.70
attackGoals_raw[1,1]       1.91    0.10   2.54  -3.27   0.21   2.10   3.70
attackGoals_raw[1,2]      -4.70    0.11   2.77  -8.87  -6.93  -5.00  -2.70
attackGoals_raw[1,3]      -3.54    0.12   3.32  -8.79  -6.17  -3.85  -1.09
attackGoals_raw[1,4]      -0.07    0.12   3.10  -6.24  -2.22  -0.04   2.04
attackGoals_raw[1,5]       0.51    0.11   2.64  -4.56  -1.24   0.44   2.21
attackGoals_raw[1,6]       1.01    0.10   2.79  -4.61  -0.93   1.11   2.93
attackGoals_raw[1,7]      -0.10    0.10   2.57  -5.12  -1.84  -0.10   1.54
attackGoals_raw[1,8]       1.38    0.13   2.66  -3.90  -0.50   1.42   3.27
attackGoals_raw[1,9]       1.37    0.06   1.92  -2.32   0.09   1

In [11]:
fit <- sflist2stanfit(sflist)

In [12]:
write.csv(print(summary(fit)), file = "fitproper.csv")

$summary
                                  mean      se_mean           sd          2.5%
delta                     8.725775e-01 0.0021204060 7.283578e-02  7.309084e-01
attackGoals_raw[1,1]      1.874774e+00 0.0817196489 2.674427e+00 -3.089846e+00
attackGoals_raw[1,2]     -1.499637e+00 0.0896254118 3.243211e+00 -7.806908e+00
attackGoals_raw[1,3]      1.403785e+00 0.0820116428 2.935338e+00 -4.421898e+00
attackGoals_raw[1,4]     -2.096955e+00 0.0914660133 2.775183e+00 -7.374858e+00
attackGoals_raw[1,5]      1.105395e+00 0.0679745454 3.124728e+00 -5.125189e+00
attackGoals_raw[1,6]      8.926727e-01 0.0702127081 2.792882e+00 -4.602424e+00
attackGoals_raw[1,7]      1.254435e+00 0.0770806245 2.854637e+00 -4.329163e+00
attackGoals_raw[1,8]      1.933899e-02 0.0672381181 2.726860e+00 -5.255428e+00
attackGoals_raw[1,9]      1.300226e-02 0.0841007431 3.148250e+00 -6.209025e+00
attackGoals_raw[1,10]    -3.084767e+00 0.0860228619 3.293843e+00 -8.662285e+00
attackGoals_raw[1,11]     1.811681e+00 0.09

# Extract parameters

In [13]:
fit.samples <- extract(fit)
write.csv(fit.samples, file = "samples.csv")

# Take the average of the mu for each team

In [14]:
# parameter estimate extractor
delta <- mean (fit.samples$delta)
muAttGoals.vec <- apply(fit.samples$muAttGoals, 2, mean) # I think the 18th team here is
  # suffering from the sum to zero constraint, maybe will dissapear with more samples

muAttBehinds.vec <- apply(fit.samples$muAttBehinds, 2, mean)
muDef.vec <- apply(fit.samples$muDef, 2, mean)

mu.ests <- matrix(c( "Goal attack mean estimates", muAttGoals.vec,"Behind attack mean estimates", muAttBehinds.vec,
                     "defend means estimates", muDef.vec), ncol = 3, byrow = F)
write.csv(mu.ests, file = "AR mean estimates.csv")

# Extract phiAtt, phiDef, attackGoals, attackBehinds, defend

In [15]:
phiAtt.vec <- mean(fit.samples$phiAtt)
phiDef.vec <- mean(fit.samples$phiDef)
std.attack.vec <- mean(fit.samples$stdAtt)
std.def.vec <- mean(fit.samples$stdDef)

goal.attack.strenghts.mat <- apply(fit.samples$attackGoals, 2:3, mean)
write.csv(goal.attack.strenghts.mat, file = "goal.attack.str.csv")

behind.attack.strengths.mat <- apply(fit.samples$attackBehinds, 2:3, mean)
write.csv(behind.attack.strengths.mat, file = "behind.attack.str.csv")

defence.strengths.mat <- apply(fit.samples$defend, 2:3, mean)
write.csv(defence.strengths.mat, file = "def.str.csv")

par.vec <- c(delta, "delta",
             phiAtt.vec, "phi.attack",
             phiDef.vec, "phi.defend",
             std.attack.vec, "std.attack",
             std.def.vec, "std.defend")

par.vec.est <- matrix(par.vec, ncol = 2, byrow = T)
write.csv(par.vec.est,  file = "parameter estimates.csv")

# Extract goalDiff, behindDiff, and totalDiff

In [16]:
avg.pred.goal.diff <- apply(fit.samples$goalDiff, 2, mean)
avg.pred.behind.diff <- apply(fit.samples$behindDiff, 2, mean)
avg.pred.total.diff <- apply(fit.samples$totalDiff, 2, mean)

In [17]:
# see if we got it right
actual.total.diff <- matchup$home.score - matchup$away.score
correct.vec <- ((avg.pred.total.diff * actual.total.diff)>0)

In [18]:
actual.total.diff
correct.vec

[1]  47  67  22  80  86  -7  93  31 -48

[1]  TRUE  TRUE  TRUE  TRUE FALSE  TRUE  TRUE  TRUE FALSE

# Calculate percentage of win, loss and draw

In [19]:
# get the percentage of win/loss

winDrawLossPer <- function(x.vec) {
  home.win.per <- mean(as.numeric(x.vec > 0))
  draw.per <- mean(as.numeric(x.vec == 0))
  away.win.per <- mean(as.numeric(x.vec < 0))
  c(home.win.per, draw.per ,away.win.per)
}

In [20]:
per.chance.mat <- apply(fit.samples$totalDiff, 2, winDrawLossPer)
per.chance.mat

iterations [,1]   [,2]   [,3]   [,4]   [,5]   [,6]   [,7]   [,8]   [,9]  
      [1,] 0.5494 0.6430 0.6156 0.5100 0.3852 0.3502 0.8412 0.5208 0.8958
      [2,] 0.0820 0.0514 0.0224 0.0246 0.0256 0.0474 0.0126 0.1318 0.0116
      [3,] 0.3686 0.3056 0.3620 0.4654 0.5892 0.6024 0.1462 0.3474 0.0926

In [21]:
# the sd ests are going to be wildly larger than they should due to not throwing out burn in
# samples, should probably change all my apply's to deal with this but ehhhhhhhh, more samples
# takes care of it for the most part
sd.ests <- round(apply(fit.samples$totalDiff,2,sd),2)

In [22]:
sim.pred.mat <- matrix(c("behind diff", avg.pred.behind.diff,
                         "goal diff", avg.pred.goal.diff,
                         "total diff", avg.pred.total.diff,
                         "home team", as.character(matchup$home.name),
                         "away team", as.character(matchup$away.name),
                         "actual result", actual.total.diff,
                         "prediction correct?", correct.vec,
                         "home win prob", per.chance.mat[1,],
                         "draw prob", per.chance.mat[2,],
                         "home loss prob", per.chance.mat[3,],
                         "simulated sd ests", sd.ests
                         ), nrow = 11, byrow = T)

write.csv(sim.pred.mat, file = "internal predictions.csv")

In [23]:
sim.pred.mat

[,1]                [,2]    [,3]    [,4]    [,5]   [,6]     [,7]    
 [1,] behind diff         -3.0422 8.3774  -6.3088 0.1428 3.3834   0.3406  
 [2,] goal diff           2.1364  1.1188  5.3706  1.5538 -2.9486  -2.1644 
 [3,] total diff          9.7762  15.0902 25.9148 9.4656 -14.3082 -12.6458
 [4,] home team           GE      HW      ES      WC     NM       WB      
 [5,] away team           SK      ME      PA      GC     CA       SY      
 [6,] actual result       47      67      22      80     86       -7      
 [7,] prediction correct? TRUE    TRUE    TRUE    TRUE   FALSE    TRUE    
 [8,] home win prob       0.5494  0.643   0.6156  0.51   0.3852   0.3502  
 [9,] draw prob           0.082   0.0514  0.0224  0.0246 0.0256   0.0474  
[10,] home loss prob      0.3686  0.3056  0.362   0.4654 0.5892   0.6024  
[11,] simulated sd ests   41.58   50.47   104.75  147.57 96.68    84.74   
      [,8]    [,9]    [,10]  
 [1,] 6.6632  -0.5268 45.0124
 [2,] 13.9754 1.5746  5.14   
 [3,] 90.5156 8.9208  75.8524
 [4,] RI      GW      AD     
 [5,] BL      FR      CW     
 [6,] 93      31      -48    
 [7,] TRUE    TRUE    FALSE  
 [8,] 0.8412  0.5208  0.8958 
 [9,] 0.0126  0.1318  0.0116 
[10,] 0.1462  0.3474  0.0926 
[11,] 196.72  39.12   140.97

In [24]:
write.csv(t(sim.pred.mat),  file = "round4_prediction.csv")